## (1) Import libraries

In [1]:
import pandas as pd
import sklearn.metrics
from pycaret.datasets import get_data

import autosklearn.classification

In [2]:
# Record version of key libraries
from importlib.metadata import version

print('auto-sklearn==%s' % version('auto-sklearn'))

auto-sklearn==0.13.0


## (2) Get data

In [3]:
# Get a list of all pre-packaged data
# get_data('index')

# Select a pre-packaged data for testing
data = get_data('diabetes')

Number of times pregnant  \
0                         6   
1                         1   
2                         8   
3                         1   
4                         0   

   Plasma glucose concentration a 2 hours in an oral glucose tolerance test  \
0                                                148                          
1                                                 85                          
2                                                183                          
3                                                 89                          
4                                                137                          

   Diastolic blood pressure (mm Hg)  Triceps skin fold thickness (mm)  \
0                                72                                35   
1                                66                                29   
2                                64                                 0   
3                                66                                23   
4                                40                                35   

   2-Hour serum insulin (mu U/ml)  \
0                               0   
1                               0   
2                               0   
3                              94   
4                             168   

   Body mass index (weight in kg/(height in m)^2)  Diabetes pedigree function  \
0                                            33.6                       0.627   
1                                            26.6                       0.351   
2                                            23.3                       0.672   
3                                            28.1                       0.167   
4                                            43.1                       2.288   

   Age (years)  Class variable  
0           50               1  
1           31               0  
2           32               1  
3           21               0  
4           33               1

In [4]:
# NOTE - all data needs to be numerical to be processed by auto-sklearn
# NOTE - categorical strings need to be converted into integers, e.g. using sklearn LabelEncoder

# Split data into X and y in numpy array (as numpy array is better supported by auto-sklearn)
X = data.iloc[:,:-1].to_numpy()
y = data.iloc[:,-1].to_numpy()

# Specify types of features - can only be either categorical or numerical. Categorical feature will get one-hot encoded
# Must be specified for each column
feat_type = [
    'Numerical', 'Numerical', 'Numerical', 'Numerical', 
    'Numerical', 'Numerical', 'Numerical', 'Numerical'
]

# Split data into training and testing data
X_train, X_test, y_train, y_test = sklearn.model_selection.train_test_split(X, y, random_state=6)

display(X)
display(y)

array([[  6.   , 148.   ,  72.   , ...,  33.6  ,   0.627,  50.   ],
       [  1.   ,  85.   ,  66.   , ...,  26.6  ,   0.351,  31.   ],
       [  8.   , 183.   ,  64.   , ...,  23.3  ,   0.672,  32.   ],
       ...,
       [  5.   , 121.   ,  72.   , ...,  26.2  ,   0.245,  30.   ],
       [  1.   , 126.   ,  60.   , ...,  30.1  ,   0.349,  47.   ],
       [  1.   ,  93.   ,  70.   , ...,  30.4  ,   0.315,  23.   ]])

array([1, 0, 1, 0, 1, 0, 1, 0, 1, 1, 0, 1, 0, 1, 1, 1, 1, 1, 0, 1, 0, 0,
       1, 1, 1, 1, 1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 1, 1, 0, 0, 0, 1,
       0, 1, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 1, 0, 0, 0, 0, 1, 0, 0, 1, 0,
       1, 0, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0,
       1, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1,
       1, 1, 0, 0, 1, 1, 1, 0, 0, 0, 1, 0, 0, 0, 1, 1, 0, 0, 1, 1, 1, 1,
       1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0,
       1, 1, 0, 0, 0, 1, 0, 0, 0, 0, 1, 1, 0, 0, 0, 0, 1, 1, 0, 0, 0, 1,
       0, 1, 0, 1, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 0, 0, 1, 1, 0, 1, 0, 1,
       1, 1, 0, 0, 0, 0, 0, 0, 1, 1, 0, 1, 0, 0, 0, 1, 1, 1, 1, 0, 1, 1,
       1, 1, 0, 0, 0, 0, 0, 1, 0, 0, 1, 1, 0, 0, 0, 1, 1, 1, 1, 0, 0, 0,
       1, 1, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 1, 0, 1, 0, 0,
       1, 0, 1, 0, 0, 1, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 1, 1, 0,
       0, 1, 0, 0, 0, 1, 1, 1, 0, 0, 1, 0, 1, 0, 1,

## (3) Setup model object

In [5]:
# Setup automl model
# NOTE - AutoSklearn2Classifier is an improved version of AutoSklearnClassifier, but currently as experimental feature
# NOTE - change resampling_strategy from default will lead to error in automl.predict()

automl = autosklearn.classification.AutoSklearnClassifier(
    time_left_for_this_task=120,
    per_run_time_limit=30,
    ensemble_size=50,
    ensemble_nbest=10,
    # resampling_strategy='cv',
    # resampling_strategy_arguments={'folds':3},
    seed=6
)

## (4) Construct model ensemble

In [6]:
# Automatically construct an ensemble of best performing models based on selected metrics
# Uses Bayesian optimisation (from SMAC python library) to tune hyperparameters and select best performing models
# Randomness seems to be quite fit in this method using default settings. Each run yield different sets of models.
automl.fit(
    X=X_train, 
    y=y_train, 
    feat_type=feat_type,
    dataset_name='diabetes'
)

print(automl.leaderboard())

[WARNING] [2021-08-08 00:47:42,503:Client-AutoMLSMBO(6)::diabetes] Dataset diabetes already in meta-data. Removing occurence.
          rank  ensemble_weight           type      cost  duration
model_id                                                          
43           1             0.46            qda  0.225131  0.542785
40           2             0.32            qda  0.230366  0.625821
33           3             0.02    extra_trees  0.246073  1.734644
42           4             0.14            qda  0.246073  0.592578
9            5             0.06  random_forest  0.256545  1.465093


## (5) Show final models in ensemble

In [7]:
print(automl.show_models())

[(0.460000, SimpleClassificationPipeline({'balancing:strategy': 'weighting', 'classifier:__choice__': 'qda', 'data_preprocessing:categorical_transformer:categorical_encoding:__choice__': 'one_hot_encoding', 'data_preprocessing:categorical_transformer:category_coalescence:__choice__': 'minority_coalescer', 'data_preprocessing:numerical_transformer:imputation:strategy': 'median', 'data_preprocessing:numerical_transformer:rescaling:__choice__': 'quantile_transformer', 'feature_preprocessor:__choice__': 'liblinear_svc_preprocessor', 'classifier:qda:reg_param': 0.10063119850312452, 'data_preprocessing:categorical_transformer:category_coalescence:minority_coalescer:minimum_fraction': 0.00010703673967305097, 'data_preprocessing:numerical_transformer:rescaling:quantile_transformer:n_quantiles': 665, 'data_preprocessing:numerical_transformer:rescaling:quantile_transformer:output_distribution': 'uniform', 'feature_preprocessor:liblinear_svc_preprocessor:C': 6031.2638749971775, 'feature_preproces

## (6) Generate predictions & test results

In [8]:
predictions = automl.predict(X_train)
print("Train accuracy score:", sklearn.metrics.accuracy_score(y_train, predictions))

predictions = automl.predict(X_test)
print("Test accuracy score:", sklearn.metrics.accuracy_score(y_test, predictions))

Train accuracy score: 0.7899305555555556
Test accuracy score: 0.7864583333333334
